In [1]:
%load_ext autoreload
%autoreload 2
from utils_benchmark_pose import *
from benchmark_pose import *

/home/mattia/miniconda3/envs/keypoint_factory/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [ ]:
_, res = eval_colmap_model(
    "/home/mattia/Desktop/Repos/wrapper_factory/benchmarks_3D/results/vggt/eth3d/terrace_2/sparse_BA",
    "/home/mattia/Desktop/Repos/wrapper_factory/benchmarks_3D/eth3d/terrace_2/sparse",
    return_df=True, thrs=[1,3,5,10])

_, res

In [ ]:
input_path = "/home/mattia/Desktop/Repos/wrapper_factory/benchmarks_3D/results/vggt/eth3d"
target_path = "/home/mattia/Desktop/Repos/wrapper_factory/benchmarks_3D/eth3d"

In [ ]:
df = eval_colmap_model_all_scenes(input_path, target_path, input_folder='sparse_BA')
df

In [2]:
for scene in sorted(os.listdir("/home/mattia/Desktop/Repos/wrapper_factory/benchmarks_3D/eth3d")):
    try:
        os.system(f"python /home/mattia/Desktop/Repos/wrapper_factory/methods/vggt/demo_colmap.py \
            --scene_dir /home/mattia/Desktop/Repos/wrapper_factory/benchmarks_3D/eth3d/{scene} \
            --output_dir /home/mattia/Desktop/Repos/wrapper_factory/benchmarks_3D/results/vggt/eth3d/{scene} \
            --imgs_dir images_by_k \
        ")

        # create database
        

    except Exception as e:
        print(f"Error processing {scene}: {e}")

Arguments: {'scene_dir': '/home/mattia/Desktop/Repos/wrapper_factory/benchmarks_3D/eth3d/botanical_garden', 'imgs_dir': 'images_by_k', 'output_dir': '/home/mattia/Desktop/Repos/wrapper_factory/benchmarks_3D/results/vggt/eth3d/botanical_garden', 'seed': 42, 'use_ba': False, 'max_reproj_error': 8.0, 'shared_camera': False, 'camera_type': 'SIMPLE_PINHOLE', 'vis_thresh': 0.2, 'query_frame_num': 8, 'max_query_pts': 4096, 'fine_tracking': True, 'conf_thres_value': 5.0}
Setting seed as: 42
Using device: cuda
Using dtype: torch.bfloat16
Loaded 30 images from /home/mattia/Desktop/Repos/wrapper_factory/benchmarks_3D/eth3d/botanical_garden/images_by_k
Model loaded
Converting to COLMAP format
Saving reconstruction to /home/mattia/Desktop/Repos/wrapper_factory/benchmarks_3D/results/vggt/eth3d/botanical_garden/sparse_wo_BA
Arguments: {'scene_dir': '/home/mattia/Desktop/Repos/wrapper_factory/benchmarks_3D/eth3d/boulders', 'imgs_dir': 'images_by_k', 'output_dir': '/home/mattia/Desktop/Repos/wrapper_fa

In [3]:
# then I have to triangulate to get colmap points

import numpy as np
import os
import h5py
import glob
import pycolmap
from pathlib import Path
from scipy.spatial.transform import Rotation as R_scipy

#####################################################################################
# Process all scenes in the phototourism dataset
#####################################################################################
orig_path = Path(
    "/home/mattia/Desktop/Repos/wrapper_factory/benchmarks_3D/eth3d"
)
res_path = Path(
    "/home/mattia/Desktop/Repos/wrapper_factory/benchmarks_3D/results/vggt/eth3d"
)

for scene in os.listdir(res_path):
    # Example usage:
    base_path  = res_path / scene 
    rec_path   = base_path / "sparse_wo_BA"
    output_dir = base_path / "sparse_colmap_BA"
    rec = pycolmap.Reconstruction(rec_path)

    images_path = orig_path / scene / "images_by_k"
    temp_path   = orig_path / scene / "temp"
    os.makedirs(temp_path, exist_ok=True)
    os.system(f"mv {images_path}/* {temp_path}/")

    for image in sorted(glob.glob(f"{temp_path}/*/*")):
        image = os.path.relpath(image, temp_path)
        # create fodler if not exists
        os.makedirs(os.path.dirname(f"{images_path}/{image}"), exist_ok=True)
        # image from temp_path to images_path
        os.system(f"mv {temp_path}/{image} {images_path}/{image}")
        camera = rec.find_image_with_name(image).camera

        # load camera intrinsics
        camera_model = camera.model.name
        params = [
            str(p) for p in camera.params
        ]  # convert to strings for COLMAP command

        # extract features using COLMAP
        os.makedirs(base_path / "colmap", exist_ok=True)
        os.system(
            f'colmap feature_extractor \
            --database_path {base_path}/colmap/database.db \
            --image_path {images_path} \
            --ImageReader.camera_model {camera_model} \
            --ImageReader.camera_params "{",".join(params)}" \
            '
        )

    os.system(f"rm -rf {temp_path}")

    os.system(
        f"colmap exhaustive_matcher --database_path {base_path}/colmap/database.db"
    )

    os.makedirs(base_path / "sparse_colmap_BA", exist_ok=True)
    os.system(
        f"colmap point_triangulator \
            --input_path {base_path}/sparse_wo_BA \
            --database_path {base_path}/colmap/database.db \
            --image_path {images_path} \
            --output_path {base_path}/sparse_colmap_BA \
            "
    )

I1013 18:33:13.168372 688647 misc.cc:44] 
Feature extraction
I1013 18:33:13.169731 688668 sift.cc:721] Creating SIFT GPU feature extractor
I1013 18:33:13.532294 688669 feature_extraction.cc:259] Processed file [1/1]
I1013 18:33:13.532323 688669 feature_extraction.cc:262]   Name:            0/DSC_0490.JPG
I1013 18:33:13.532325 688669 feature_extraction.cc:271]   Dimensions:      6208 x 4138
I1013 18:33:13.532326 688669 feature_extraction.cc:274]   Camera:          #1 - PINHOLE
I1013 18:33:13.532328 688669 feature_extraction.cc:277]   Focal Length:    3981.00px (Prior)
I1013 18:33:13.532332 688669 feature_extraction.cc:281]   Features:        9281
I1013 18:33:13.630157 688647 timer.cc:91] Elapsed time: 0.008 [minutes]
I1013 18:33:13.736963 688680 misc.cc:44] 
Feature extraction
I1013 18:33:13.737989 688701 sift.cc:721] Creating SIFT GPU feature extractor
I1013 18:33:13.739243 688702 feature_extraction.cc:259] Processed file [1/2]
I1013 18:33:13.739255 688702 feature_extraction.cc:262]   